# Business Problem

I like to eat sushi as well as make sushi. So I want open a sushi restaurant in New York. There are in total 62 counties in New York and I don't know which one should I choose

# Data Description

To choose the optimal locations, I need to consider following points:
    1. Household income
    2. Competitors nearby(sushi restaurant)
    3. Non-sushi restaurant
    4. Crime rates
    5. Transportation facilities (Parking place, bus station, train station)
    6. Entertainmaint (cafe shops, bars, cinema, hotels, Museum, theater,etc.)


To get the data, following data sources are used:

    1. Household income
       Household income and density (https://en.wikipedia.org/wiki/List_of_New_York_locations_by_per_capita_income)
       
    2. Competitors nearby(sushi restaurant)
       From foursquare
       
    3. Non-sushi restaurant
       From foursquare
       
    4. Crime rates
       Crime rates in New York (https://www.criminaljustice.ny.gov/crimnet/ojsa/countycrimestats.htm)
       
    5. Transportation facilities (Parking place, bus station, train station)
       From foursquare
       
    6. Entertainmaint (cafe shops, bars, cinema, hotels, Museum, theater,etc.)
       From foursquare


In [4]:
import pandas as pd
#!conda install -c conda-forge geopy --yes
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
# Matplotlib and associated plotting modules

import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

import json # library to handle JSON files
import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# 1. Import Data

## Import Counties Data and Income Data

Import counties data

In [79]:
# Import counties data
url_counties= "https://en.wikipedia.org/wiki/List_of_counties_in_New_York"
url_incomes = "https://en.wikipedia.org/wiki/List_of_New_York_locations_by_per_capita_income"
df_counties = pd.read_html(url_counties)[2]
df_counties.head()

County  FIPS Code[3] County seat[5]  Est.[5]  \
0       Albany County             1         Albany     1683   
1     Allegany County             3        Belmont     1806   
2        Bronx County             5           none  1914[7]   
3       Broome County             7     Binghamton     1806   
4  Cattaraugus County             9  Little Valley     1808   

                                      Formed from[1]  \
0  One of 12 original counties created in the New...   
1                                     Genesee County   
2                                    New York County   
3                                       Tioga County   
4                                     Genesee County   

                                        Named for[2]  Density (Pop./mi2)  \
0  James II of England (James VII of Scotland) (1...              570.74   
1          A variant spelling of the Allegheny River               47.34   
2  Jonas Bronck (1600?–1643), an early settler of...            24118.20   
3  John Broome (1738–1810), fourth Lieutenant Gov...              280.56   
4  A word from an uncertain Iroquoian language me...               61.31   

   Pop. (2010)[6]                 Area[5]  Map  
0          304204    533 sq mi(1,380 km2)  NaN  
1           48946  1,034 sq mi(2,678 km2)  NaN  
2         1385108    57.43 sq mi(149 km2)  NaN  
3          200600    715 sq mi(1,852 km2)  NaN  
4           80317  1,310 sq mi(3,393 km2)  NaN

Import incomes of counties

In [72]:
df_incomes = pd.read_html(url_incomes)[1]
df_incomes.head()

Rank           County Per capitaincome Medianhouseholdincome  \
0   1.0  New York County         $111,386               $64,971   
1   2.0      Westchester          $73,159               $79,619   
2   3.0           Nassau          $41,387               $93,613   
3   4.0           Putnam          $37,915               $89,218   
4   5.0          Suffolk          $35,755               $84,506   

  Medianfamilyincome  Population  Number ofhouseholds  
0            $75,629     1585873               763846  
1           $100,863      949113               347232  
2           $107,934     1339532               448528  
3           $101,576       99710                35041  
4            $96,220     1493350               499922

## Import Data in Foursquare

In [26]:
CLIENT_ID ='HM5S5EODZ15DE2YDYC4302GQGC0RGEAKMBMPFGA0BESRBYFV' # your Foursquare ID
CLIENT_SECRET = 'NSP3B2TY1MVJWT34E3THE1PGA54DIQIPEDZSVCASHAYT2UMY' # your Foursquare Secret
VERSION = '20200608' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value
ACCESS_TOKEN = 'ZN4BUBVO5CT5R0Q0HNG01PIDABCLLAXLAYKSXXH0VO2N1PA2' # your FourSquare Access

In [27]:
def getNearbyVenues(names, latitudes, longitudes, radius=5000):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [126]:
location = pd.read_csv(r"C:\H Digitalisierung\Coursera course\IBM Data Science\Capstone Final Project\Dataset Needed\Geospatial_Coordinates.csv")
#location = pd.read_csv("https://cocl.us/Geospatial_data")

In [15]:
location.head()

County   Latitude  Longitude
0       Albany  42.662094 -73.849075
1     Allegany  42.232937 -78.026093
2        Bronx  40.837222 -73.886111
3       Broome  42.136986 -75.888313
4  Cattaraugus  42.230316 -78.638206

In [28]:
county_venues = getNearbyVenues(names=location['County'],
                         latitudes=location['Latitude'],
                         longitudes=location['Longitude'])

Albany
Allegany
Bronx
Broome
Cattaraugus
Cayuga
Chautauqua
Chemung
Chenango
Clinton
Columbia
Cortland
Delaware
Dutchess
Erie
Essex
Franklin
Fulton
Genesee
Greene
Hamilton
Herkimer
Jefferson
Kings
Lewis
Livingston
Madison
Monroe
Montgomery
Nassau
New York
Niagara
Oneida
Onondaga
Ontario
Orange
Orleans
Oswego
Otsego
Putnam
Queens
Rensselaer
Richmond
Rockland
St. Lawrence
Saratoga
Schenectady
Schoharie
Schuyler
Seneca
Steuben
Suffolk
Sullivan
Tioga
Tompkins
Ulster
Warren
Washington
Wayne
Westchester
Wyoming
Yates


In [37]:
county_venues.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0       Albany              42.662094              -73.849075   
1       Albany              42.662094              -73.849075   
2       Albany              42.662094              -73.849075   
3       Albany              42.662094              -73.849075   
4       Albany              42.662094              -73.849075   

                         Venue  Venue Latitude  Venue Longitude Venue Category  
0      Capital Hills at Albany       42.651124       -73.821128    Golf Course  
1  Black & Blue Steak and Crab       42.680904       -73.838403     Steakhouse  
2                    Five Guys       42.682244       -73.842205   Burger Joint  
3                  Blaze Pizza       42.683463       -73.840269    Pizza Place  
4            The Hot Yoga Spot       42.685378       -73.840233    Yoga Studio

In [30]:
county_venues.shape

(2090, 7)

## Import crime data

In [102]:
df_crime = pd.read_excel (r'C:\H Digitalisierung\Coursera course\IBM Data Science\Capstone Final Project\Dataset Needed\new_york_crime_2019.xls')
df_crime.head()

County  Violent Count  Property Count
0       Albany           1017            7008
1     Allegany             61             395
2        Bronx          13157           22098
3       Broome            621            4548
4  Cattaraugus            151             777

# 2. Data Cleaning

In [56]:
df_incomes.dtypes

Rank                     float64
County                    object
Per capitaincome          object
Medianhouseholdincome     object
Medianfamilyincome        object
Population                 int64
Number ofhouseholds        int64
dtype: object

In [73]:
# Delete the rows which are not counties in New York
df_incomes.dropna(subset=["Rank"], inplace=True)
df_incomes.shape

(62, 7)

In [74]:
df_incomes["County"] = df_incomes["County"]+ " County"
df_incomes.head()

Rank                  County Per capitaincome Medianhouseholdincome  \
0   1.0  New York County County         $111,386               $64,971   
1   2.0      Westchester County          $73,159               $79,619   
2   3.0           Nassau County          $41,387               $93,613   
3   4.0           Putnam County          $37,915               $89,218   
4   5.0          Suffolk County          $35,755               $84,506   

  Medianfamilyincome  Population  Number ofhouseholds  
0            $75,629     1585873               763846  
1           $100,863      949113               347232  
2           $107,934     1339532               448528  
3           $101,576       99710                35041  
4            $96,220     1493350               499922

In [75]:
df_incomes["County"].replace({'New York County County': 'New York County'}, inplace=True)
df_incomes.head()

Rank              County Per capitaincome Medianhouseholdincome  \
0   1.0     New York County         $111,386               $64,971   
1   2.0  Westchester County          $73,159               $79,619   
2   3.0       Nassau County          $41,387               $93,613   
3   4.0       Putnam County          $37,915               $89,218   
4   5.0      Suffolk County          $35,755               $84,506   

  Medianfamilyincome  Population  Number ofhouseholds  
0            $75,629     1585873               763846  
1           $100,863      949113               347232  
2           $107,934     1339532               448528  
3           $101,576       99710                35041  
4            $96,220     1493350               499922

Merge df_counties and df_incomes

In [112]:
df_dummy = pd.merge(df_counties, df_incomes, on="County")
df_dummy.shape

(62, 16)

In [113]:
df_dummy.head(1)

County  FIPS Code[3] County seat[5] Est.[5]  \
0  Albany County             1         Albany    1683   

                                      Formed from[1]  \
0  One of 12 original counties created in the New...   

                                        Named for[2]  Density (Pop./mi2)  \
0  James II of England (James VII of Scotland) (1...              570.74   

   Pop. (2010)[6]               Area[5]  Map  Rank Per capitaincome  \
0          304204  533 sq mi(1,380 km2)  NaN  10.0          $30,863   

  Medianhouseholdincome Medianfamilyincome  Population  Number ofhouseholds  
0               $56,090            $76,159      304204               126251

Merge df_dummy with df_crime

In [103]:
df_crime["Crime_sum"] = df_crime.sum(axis=1)
df_crime=df_crime[["County","Crime_sum"]]
df_crime["County"] = df_crime["County"]+ " County"
df_crime.head()

County  Crime_sum
0       Albany County       8025
1     Allegany County        456
2        Bronx County      35255
3       Broome County       5169
4  Cattaraugus County        928

In [163]:
df_all=pd.merge(df_dummy, df_crime, on="County")
df_all.shape

(62, 17)

In [164]:
df_all.head(2)

County  FIPS Code[3] County seat[5] Est.[5]  \
0    Albany County             1         Albany    1683   
1  Allegany County             3        Belmont    1806   

                                      Formed from[1]  \
0  One of 12 original counties created in the New...   
1                                     Genesee County   

                                        Named for[2]  Density (Pop./mi2)  \
0  James II of England (James VII of Scotland) (1...              570.74   
1          A variant spelling of the Allegheny River               47.34   

   Pop. (2010)[6]                 Area[5]  Map  Rank Per capitaincome  \
0          304204    533 sq mi(1,380 km2)  NaN  10.0          $30,863   
1           48946  1,034 sq mi(2,678 km2)  NaN  60.0          $20,058   

  Medianhouseholdincome Medianfamilyincome  Population  Number ofhouseholds  \
0               $56,090            $76,159      304204               126251   
1               $41,305            $49,864       48946                18208   

   Crime_sum  
0       8025  
1        456

In [165]:
df_all.drop(['FIPS Code[3]', 'County seat[5]','Est.[5]','Per capitaincome','Formed from[1]','Named for[2]','Named for[2]','Pop. (2010)[6]','Area[5]','Map','Rank','Medianfamilyincome','Number ofhouseholds'], axis=1,inplace=True)

In [166]:
df_all.head()

County  Density (Pop./mi2) Medianhouseholdincome  Population  \
0       Albany County              570.74               $56,090      304204   
1     Allegany County               47.34               $41,305       48946   
2        Bronx County            24118.20               $34,264     1385108   
3       Broome County              280.56               $44,457      200600   
4  Cattaraugus County               61.31               $42,466       80317   

   Crime_sum  
0       8025  
1        456  
2      35255  
3       5169  
4        928

Merge df_all with county_venues

In [192]:
county_venues.rename(columns={"Neighborhood": "County", "Neighborhood Latitude": "County Latitude","Neighborhood Longitude": "County Lagitude"},inplace=True)
county_venues["County"] = county_venues["County"]+ " County"

In [194]:
county_venues.head(5)

County  County Latitude  \
0  Albany County County County County County        42.662094   
1  Albany County County County County County        42.662094   
2  Albany County County County County County        42.662094   
3  Albany County County County County County        42.662094   
4  Albany County County County County County        42.662094   

   County Lagitude                        Venue  Venue Latitude  \
0       -73.849075      Capital Hills at Albany       42.651124   
1       -73.849075  Black & Blue Steak and Crab       42.680904   
2       -73.849075                    Five Guys       42.682244   
3       -73.849075                  Blaze Pizza       42.683463   
4       -73.849075            The Hot Yoga Spot       42.685378   

   Venue Longitude Venue Category  
0       -73.821128    Golf Course  
1       -73.838403     Steakhouse  
2       -73.842205   Burger Joint  
3       -73.840269    Pizza Place  
4       -73.840233    Yoga Studio

In [183]:
result = pd.merge(county_venues, df_all, on="County", how="outer")
result.shape

(2090, 11)

In [193]:
result.head()

County  County Latitude  County Lagitude  \
0  Albany County        42.662094       -73.849075   
1  Albany County        42.662094       -73.849075   
2  Albany County        42.662094       -73.849075   
3  Albany County        42.662094       -73.849075   
4  Albany County        42.662094       -73.849075   

                         Venue  Venue Latitude  Venue Longitude  \
0      Capital Hills at Albany       42.651124       -73.821128   
1  Black & Blue Steak and Crab       42.680904       -73.838403   
2                    Five Guys       42.682244       -73.842205   
3                  Blaze Pizza       42.683463       -73.840269   
4            The Hot Yoga Spot       42.685378       -73.840233   

  Venue Category  Density (Pop./mi2) Medianhouseholdincome  Population  \
0    Golf Course              570.74               $56,090      304204   
1     Steakhouse              570.74               $56,090      304204   
2   Burger Joint              570.74               $56,090      304204   
3    Pizza Place              570.74               $56,090      304204   
4    Yoga Studio              570.74               $56,090      304204   

   Crime_sum  
0       8025  
1       8025  
2       8025  
3       8025  
4       8025

# 3. Exploratory Data Analysis

In [199]:
df_all.describe()

Density (Pop./mi2)    Population     Crime_sum
count           62.000000  6.200000e+01     62.000000
mean          2095.142258  3.125500e+05   5415.096774
std           7442.517188  5.323563e+05  10644.444808
min              2.670000  4.836000e+03     29.000000
25%             67.495000  5.124350e+04    591.500000
50%            103.185000  9.130100e+04   1141.500000
75%            394.145000  2.310602e+05   3906.500000
max          46961.000000  2.504700e+06  49858.000000

In [202]:
result.describe()

County Latitude  County Lagitude  Venue Latitude  Venue Longitude  \
count      2090.000000      2090.000000     2090.000000      2090.000000   
mean         41.884151       -75.149371       41.884371       -75.151290   
std           1.010649         1.732318        1.013505         1.733567   
min          40.571944       -79.410000       40.535929       -79.428179   
25%          40.837222       -76.470000       40.830228       -76.482311   
50%          42.136986       -74.146944       42.102905       -74.146340   
75%          42.750000       -73.866667       42.784395       -73.854672   
max          44.740000       -72.680000       44.722553       -72.622421   

       Density (Pop./mi2)    Population     Crime_sum  
count         2090.000000  2.090000e+03   2090.000000  
mean          5960.911665  7.275079e+05  13142.672727  
std          11796.094818  7.365939e+05  15157.938029  
min              2.670000  4.836000e+03     29.000000  
25%            193.630000  1.079310e+05   1855.000000  
50%            579.440000  3.728130e+05   5184.000000  
75%           2957.020000  1.339532e+06  18157.000000  
max          46961.000000  2.504700e+06  49858.000000

In [205]:
address = 'New York'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of new york are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of new york are 40.7127281, -74.0060152.


In [209]:
# create map using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, borough, neighborhood in zip(result['Venue Latitude'], result['Venue Longitude'], result['County'], result['Venue']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

In [211]:
# one hot encoding
newyork_onehot = pd.get_dummies(result[['Venue Category']], prefix="", prefix_sep="")

# add county column back to dataframe
newyork_onehot['County'] = result['County']

newyork_onehot = newyork_onehot[['County']+ [ col for col in newyork_onehot.columns if col != 'County' ]]
newyork_onehot.head()

County  Accessories Store  Airport  American Restaurant  \
0  Albany County                  0        0                    0   
1  Albany County                  0        0                    0   
2  Albany County                  0        0                    0   
3  Albany County                  0        0                    0   
4  Albany County                  0        0                    0   

   Animal Shelter  Antique Shop  Aquarium  Arepa Restaurant  \
0               0             0         0                 0   
1               0             0         0                 0   
2               0             0         0                 0   
3               0             0         0                 0   
4               0             0         0                 0   

   Argentinian Restaurant  Art Gallery  ...  Waterfront  Weight Loss Center  \
0                       0            0  ...           0                   0   
1                       0            0  ...           0                   0   
2                       0            0  ...           0                   0   
3                       0            0  ...           0                   0   
4                       0            0  ...           0                   0   

   Wine Bar  Wine Shop  Winery  Wings Joint  Women's Store  Yoga Studio  Zoo  \
0         0          0       0            0              0            0    0   
1         0          0       0            0              0            0    0   
2         0          0       0            0              0            0    0   
3         0          0       0            0              0            0    0   
4         0          0       0            0              0            1    0   

   Zoo Exhibit  
0            0  
1            0  
2            0  
3            0  
4            0  

[5 rows x 302 columns]

In [215]:
newyork_onehot.shape

(2090, 302)

In [262]:
newyork_grouped = newyork_onehot.groupby('County').sum()
newyork_grouped.shape

(62, 301)

In [263]:
newyork_grouped.head()

Accessories Store  Airport  American Restaurant  \
County                                                                
Albany County                       0        0                    3   
Allegany County                     0        0                    1   
Bronx County                        0        0                    1   
Broome County                       0        0                    3   
Cattaraugus County                  0        0                    1   

                    Animal Shelter  Antique Shop  Aquarium  Arepa Restaurant  \
County                                                                         
Albany County                    0             0         0                 0   
Allegany County                  0             0         0                 0   
Bronx County                     0             0         0                 1   
Broome County                    0             0         0                 0   
Cattaraugus County               0             0         0                 0   

                    Argentinian Restaurant  Art Gallery  Art Museum  ...  \
County                                                               ...   
Albany County                            0            0           0  ...   
Allegany County                          0            0           0  ...   
Bronx County                             0            0           1  ...   
Broome County                            0            1           0  ...   
Cattaraugus County                       0            0           0  ...   

                    Waterfront  Weight Loss Center  Wine Bar  Wine Shop  \
County                                                                    
Albany County                0                   1         1          0   
Allegany County              0                   0         0          0   
Bronx County                 0                   0         0          0   
Broome County                0                   0         1          0   
Cattaraugus County           0                   0         0          0   

                    Winery  Wings Joint  Women's Store  Yoga Studio  Zoo  \
County                                                                     
Albany County            0            0              1            1    0   
Allegany County          0            0              0            0    0   
Bronx County             0            0              0            0    6   
Broome County            0            0              0            0    0   
Cattaraugus County       0            1              0            0    0   

                    Zoo Exhibit  
County                           
Albany County                 0  
Allegany County               0  
Bronx County                  4  
Broome County                 0  
Cattaraugus County            0  

[5 rows x 301 columns]

In [264]:
df_compare=pd.merge(df_all, newyork_grouped, on="County")
df_compare.head()

County  Density (Pop./mi2) Medianhouseholdincome  Population  \
0       Albany County              570.74               $56,090      304204   
1     Allegany County               47.34               $41,305       48946   
2        Bronx County            24118.20               $34,264     1385108   
3       Broome County              280.56               $44,457      200600   
4  Cattaraugus County               61.31               $42,466       80317   

   Crime_sum  Accessories Store  Airport  American Restaurant  Animal Shelter  \
0       8025                  0        0                    3               0   
1        456                  0        0                    1               0   
2      35255                  0        0                    1               0   
3       5169                  0        0                    3               0   
4        928                  0        0                    1               0   

   Antique Shop  ...  Waterfront  Weight Loss Center  Wine Bar  Wine Shop  \
0             0  ...           0                   1         1          0   
1             0  ...           0                   0         0          0   
2             0  ...           0                   0         0          0   
3             0  ...           0                   0         1          0   
4             0  ...           0                   0         0          0   

   Winery  Wings Joint  Women's Store  Yoga Studio  Zoo  Zoo Exhibit  
0       0            0              1            1    0            0  
1       0            0              0            0    0            0  
2       0            0              0            0    6            4  
3       0            0              0            0    0            0  
4       0            1              0            0    0            0  

[5 rows x 306 columns]

In [220]:
df_compare.shape

(62, 306)

In [232]:
index = df_compare.columns

In [236]:
venue_all = [str(x) for x in index.tolist()]
venue_all

['County',
 'Density (Pop./mi2)',
 'Medianhouseholdincome',
 'Population',
 'Crime_sum',
 'Accessories Store',
 'Airport',
 'American Restaurant',
 'Animal Shelter',
 'Antique Shop',
 'Aquarium',
 'Arepa Restaurant',
 'Argentinian Restaurant',
 'Art Gallery',
 'Art Museum',
 'Arts & Crafts Store',
 'Asian Restaurant',
 'Astrologer',
 'Athletics & Sports',
 'Austrian Restaurant',
 'Auto Garage',
 'Automotive Shop',
 'BBQ Joint',
 'Baby Store',
 'Bagel Shop',
 'Bakery',
 'Bank',
 'Bar',
 'Baseball Field',
 'Baseball Stadium',
 'Basketball Court',
 'Beach',
 'Beach Bar',
 'Bed & Breakfast',
 'Beer Bar',
 'Beer Garden',
 'Beer Store',
 'Belgian Restaurant',
 'Big Box Store',
 'Bistro',
 'Boat or Ferry',
 'Bookstore',
 'Botanical Garden',
 'Boutique',
 'Bowling Alley',
 'Bowling Green',
 'Boxing Gym',
 'Brazilian Restaurant',
 'Breakfast Spot',
 'Brewery',
 'Bridge',
 'Bubble Tea Shop',
 'Burger Joint',
 'Burmese Restaurant',
 'Business Service',
 'Butcher',
 'Café',
 'Cajun / Creole Restau

### Existing Sushi Restaurant
Here Japanese restaurant can also sell Sushi, so also consider japanise restaurant

In [279]:
matches_sushi = ["Sushi", "sushi", "Japan", "japan"]
Sushi = []
for string in venue_all:
     if any(x in string for x in matches_sushi):
     #if i.find( "Sushi")!=-1:
           Sushi.append(string)
Sushi

['Japanese Restaurant', 'Sushi Restaurant']

In [289]:
df_compare["Existing Sushi Restaurant"]= df_compare["Sushi Restaurant"] + df_compare["Japanese Restaurant"]
df_compare

County  Density (Pop./mi2) Medianhouseholdincome  Population  \
0        Albany County              570.74               $56,090      304204   
1      Allegany County               47.34               $41,305       48946   
2         Bronx County            24118.20               $34,264     1385108   
3        Broome County              280.56               $44,457      200600   
4   Cattaraugus County               61.31               $42,466       80317   
..                 ...                 ...                   ...         ...   
57   Washington County               74.72               $48,327       63216   
58        Wayne County               67.75               $52,562       93772   
59  Westchester County             1898.23               $79,619      949113   
60      Wyoming County               70.73               $50,075       42155   
61        Yates County               67.41               $46,822       25348   

    Crime_sum  Accessories Store  Airport  American Restaurant  \
0        8025                  0        0                    3   
1         456                  0        0                    1   
2       35255                  0        0                    1   
3        5169                  0        0                    3   
4         928                  0        0                    1   
..        ...                ...      ...                  ...   
57        321                  0        0                    0   
58       1220                  0        0                    0   
59       9637                  0        0                    6   
60        257                  0        0                    0   
61        187                  0        0                    2   

    Animal Shelter  Antique Shop  ...  Weight Loss Center  Wine Bar  \
0                0             0  ...                   1         1   
1                0             0  ...                   0         0   
2                0             0  ...                   0         0   
3                0             0  ...                   0         1   
4                0             0  ...                   0         0   
..             ...           ...  ...                 ...       ...   
57               0             0  ...                   0         0   
58               0             0  ...                   0         0   
59               0             0  ...                   0         1   
60               0             0  ...                   0         0   
61               0             0  ...                   0         0   

    Wine Shop  Winery  Wings Joint  Women's Store  Yoga Studio  Zoo  \
0           0       0            0              1            1    0   
1           0       0            0              0            0    0   
2           0       0            0              0            0    6   
3           0       0            0              0            0    0   
4           0       0            1              0            0    0   
..        ...     ...          ...            ...          ...  ...   
57          0       0            0              0            0    0   
58          0       0            0              0            0    0   
59          1       0            0              0            0    0   
60          0       0            0              0            0    0   
61          0       0            0              0            0    0   

    Zoo Exhibit  Existing Sushi Restaurant  
0             0                          4  
1             0                          0  
2             4                          1  
3             0                          1  
4             0                          0  
..          ...                        ...  
57            0                          0  
58            0                          0  
59            0                          2  
60            0                          0  
61            0                          0  

[62 rows x 307 

### Similar business

In [305]:
matches_restaurant = ["Restaurant", "restaurant"]
Restaurant = []
for string in venue_all:
     if any(x in string for x in matches_restaurant):
     #if i.find( "Sushi")!=-1:
           Restaurant.append(string)
print ("The lenth of all restaurant is:",len(Restaurant))
        
for i in Restaurant:
    if i in Sushi:
        Restaurant.remove(i)

print ("The lenth without sushi restaurant is:",len(Restaurant))

The lenth of all restaurant is: 52
The lenth without sushi restaurant is: 50


In [306]:
df_compare['Restaurant exclusive sushi']= df_compare[Restaurant].sum(axis=1)
df_compare.head()

County  Density (Pop./mi2) Medianhouseholdincome  Population  \
0       Albany County              570.74               $56,090      304204   
1     Allegany County               47.34               $41,305       48946   
2        Bronx County            24118.20               $34,264     1385108   
3       Broome County              280.56               $44,457      200600   
4  Cattaraugus County               61.31               $42,466       80317   

   Crime_sum  Accessories Store  Airport  American Restaurant  Animal Shelter  \
0       8025                  0        0                    3               0   
1        456                  0        0                    1               0   
2      35255                  0        0                    1               0   
3       5169                  0        0                    3               0   
4        928                  0        0                    1               0   

   Antique Shop  ...  Wine Bar  Wine Shop  Winery  Wings Joint  Women's Store  \
0             0  ...         1          0       0            0              1   
1             0  ...         0          0       0            0              0   
2             0  ...         0          0       0            0              0   
3             0  ...         1          0       0            0              0   
4             0  ...         0          0       0            1              0   

   Yoga Studio  Zoo  Zoo Exhibit  Existing Sushi Restaurant  \
0            1    0            0                          4   
1            0    0            0                          0   
2            0    6            4                          1   
3            0    0            0                          1   
4            0    0            0                          0   

   Restaurant exclusive sushi  
0                          15  
1                           1  
2                          17  
3                          18  
4                           2  

[5 rows x 308 columns]

### Facilities including parking station, bus station, train station

In [314]:
matches_facility = ["parking","Parking","Station","station"]
facility = []
for string in venue_all:
     if any(x in string for x in matches_facility):
     #if i.find( "Sushi")!=-1:
           facility.append(string)
facility

['Gas Station', 'Parking', 'Train Station']

In [318]:
df_compare['Trasportation Facilities']= df_compare[['Parking', 'Train Station']].sum(axis=1)
df_compare.head()

County  Density (Pop./mi2) Medianhouseholdincome  Population  \
0       Albany County              570.74               $56,090      304204   
1     Allegany County               47.34               $41,305       48946   
2        Bronx County            24118.20               $34,264     1385108   
3       Broome County              280.56               $44,457      200600   
4  Cattaraugus County               61.31               $42,466       80317   

   Crime_sum  Accessories Store  Airport  American Restaurant  Animal Shelter  \
0       8025                  0        0                    3               0   
1        456                  0        0                    1               0   
2      35255                  0        0                    1               0   
3       5169                  0        0                    3               0   
4        928                  0        0                    1               0   

   Antique Shop  ...  Wine Shop  Winery  Wings Joint  Women's Store  \
0             0  ...          0       0            0              1   
1             0  ...          0       0            0              0   
2             0  ...          0       0            0              0   
3             0  ...          0       0            0              0   
4             0  ...          0       0            1              0   

   Yoga Studio  Zoo  Zoo Exhibit  Existing Sushi Restaurant  \
0            1    0            0                          4   
1            0    0            0                          0   
2            0    6            4                          1   
3            0    0            0                          1   
4            0    0            0                          0   

   Restaurant exclusive sushi  Trasportation Facilities  
0                          15                         0  
1                           1                         0  
2                          17                         0  
3                          18                         0  
4                           2                         0  

[5 rows x 309 columns]

### Entertainment

In [322]:
matches_ent = ["Gym","Bar","Stadium","Museum","Concert","Studio","Cinema","Theater","Shopping Mall","Spa","Movie","Pub",
               "Golf","Gallery","Café","Art","Sport","Hotel"]
entertainment = []
for string in venue_all:
     if any(x in string for x in matches_ent):
     #if i.find( "Sushi")!=-1:
           entertainment.append(string)
entertainment

['Art Gallery',
 'Art Museum',
 'Arts & Crafts Store',
 'Athletics & Sports',
 'Bar',
 'Baseball Stadium',
 'Beach Bar',
 'Beer Bar',
 'Boxing Gym',
 'Café',
 'Cocktail Bar',
 'College Arts Building',
 'College Gym',
 'College Stadium',
 'Concert Hall',
 'Cycle Studio',
 'Dance Studio',
 'Disc Golf',
 'Dive Bar',
 'Event Space',
 'Football Stadium',
 'Gay Bar',
 'Golf Course',
 'Gym',
 'Gym / Fitness Center',
 'Gymnastics Gym',
 'History Museum',
 'Hotel',
 'Hotel Bar',
 'Indie Movie Theater',
 'Irish Pub',
 'Juice Bar',
 'Karaoke Bar',
 'Martial Arts School',
 'Massage Studio',
 'Mini Golf',
 'Movie Theater',
 'Museum',
 'Performing Arts Venue',
 'Pub',
 'Public Art',
 'Salon / Barbershop',
 'Science Museum',
 'Shopping Mall',
 'Spa',
 'Spanish Restaurant',
 'Sporting Goods Shop',
 'Sports Bar',
 'Sports Club',
 'Tennis Stadium',
 'Theater',
 'Wine Bar',
 'Yoga Studio']

In [336]:
df_compare['Entertainment']= df_compare[entertainment].sum(axis=1)
df_compare.rename(columns={"Density (Pop./mi2)": "Density"},inplace = True)
df_compare.head()

County   Density Medianhouseholdincome  Population  Crime_sum  \
0       Albany County    570.74               $56,090      304204       8025   
1     Allegany County     47.34               $41,305       48946        456   
2        Bronx County  24118.20               $34,264     1385108      35255   
3       Broome County    280.56               $44,457      200600       5169   
4  Cattaraugus County     61.31               $42,466       80317        928   

   Accessories Store  Airport  American Restaurant  Animal Shelter  \
0                  0        0                    3               0   
1                  0        0                    1               0   
2                  0        0                    1               0   
3                  0        0                    3               0   
4                  0        0                    1               0   

   Antique Shop  ...  Winery  Wings Joint  Women's Store  Yoga Studio  Zoo  \
0             0  ...       0            0              1            1    0   
1             0  ...       0            0              0            0    0   
2             0  ...       0            0              0            0    6   
3             0  ...       0            0              0            0    0   
4             0  ...       0            1              0            0    0   

   Zoo Exhibit  Existing Sushi Restaurant  Restaurant exclusive sushi  \
0            0                          4                          15   
1            0                          0                           1   
2            4                          1                          17   
3            0                          1                          18   
4            0                          0                           2   

   Trasportation Facilities  Entertainment  
0                         0             21  
1                         0              0  
2                         0             13  
3                         0             28  
4                         0              2  

[5 rows x 310 columns]

In [489]:
df_model[df_model.columns[2]] = df_model[df_model.columns[2]].replace('[\$,]', '', regex=True).astype(float)

<ipython-input-489-423346e991d3>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_model[df_model.columns[2]] = df_model[df_model.columns[2]].replace('[\$,]', '', regex=True).astype(float)


In [490]:
df_model.dtypes

County                         object
Density                       float64
Medianhouseholdincome         float64
Crime_sum                       int64
Existing Sushi Restaurant       uint8
Restaurant exclusive sushi      int64
Trasportation Facilities        int64
Entertainment                   int64
dtype: object

In [491]:
df_model.head(1)

County  Density  Medianhouseholdincome  Crime_sum  \
0  Albany County   570.74                56090.0       8025   

   Existing Sushi Restaurant  Restaurant exclusive sushi  \
0                          4                          15   

   Trasportation Facilities  Entertainment  
0                         0             21

In [492]:
df_model = df_model.drop('County', axis=1)
df_model.head()

Density  Medianhouseholdincome  Crime_sum  Existing Sushi Restaurant  \
0    570.74                56090.0       8025                          4   
1     47.34                41305.0        456                          0   
2  24118.20                34264.0      35255                          1   
3    280.56                44457.0       5169                          1   
4     61.31                42466.0        928                          0   

   Restaurant exclusive sushi  Trasportation Facilities  Entertainment  
0                          15                         0             21  
1                           1                         0              0  
2                          17                         0             13  
3                          18                         0             28  
4                           2                         0              2

Let's normalize the dataset:

In [493]:
from sklearn.preprocessing import StandardScaler
import numpy as np
X = df_model.values[:,1:]
X = np.nan_to_num(X)
cluster_dataset = StandardScaler().fit_transform(X)
cluster_dataset

array([[ 0.30811552,  0.24719081,  4.4586496 ,  0.94521812, -0.22549381,
         2.05044253],
       [-0.89018848, -0.46968912, -0.47771246, -0.54650793, -0.22549381,
        -0.7074874 ],
       [-1.46085189,  2.82621582,  0.75637806,  1.15832184, -0.22549381,
         0.99980256],
       [-0.6347232 , -0.02330847,  0.75637806,  1.2648737 , -0.22549381,
         2.96975251],
       [-0.79609102, -0.42498475, -0.47771246, -0.43995607, -0.22549381,
        -0.44482741],
       [-0.31393272, -0.39808636, -0.47771246, -0.65305979, -0.22549381,
        -0.57615741],
       [-0.94416687, -0.24825098, -0.47771246, -0.65305979, -0.22549381,
        -0.44482741],
       [-0.63107601, -0.35915947,  0.75637806, -0.54650793, -0.22549381,
        -0.7074874 ],
       [-0.6763822 , -0.43862337, -0.47771246, -0.65305979, -0.22549381,
        -0.7074874 ],
       [-0.38898375, -0.4020643 , -0.47771246, -0.65305979, -0.22549381,
        -0.57615741],
       [ 0.26402507, -0.44525326, -0.47771246, -0.

# 4. Model Development

Cluster Neighborhoods

In [544]:
num_clusters=8

k_means = KMeans(init="k-means++", n_clusters=num_clusters, n_init=12)
k_means.fit(cluster_dataset)
labels = k_means.labels_

In [545]:
df_model['Labels']=labels
df_model.head()

Density  Medianhouseholdincome  Crime_sum  Existing Sushi Restaurant  \
0    570.74                56090.0       8025                          4   
1     47.34                41305.0        456                          0   
2  24118.20                34264.0      35255                          1   
3    280.56                44457.0       5169                          1   
4     61.31                42466.0        928                          0   

   Restaurant exclusive sushi  Trasportation Facilities  Entertainment  Labels  
0                          15                         0             21       2  
1                           1                         0              0       0  
2                          17                         0             13       3  
3                          18                         0             28       5  
4                           2                         0              2       0

In [546]:
conclusion = df_model.groupby('Labels').mean()
conclusion

Density  Medianhouseholdincome     Crime_sum  \
Labels                                                      
0         110.699744           47399.205128   1447.000000   
1        2514.385000           82205.500000  11487.500000   
2         659.880000           51731.000000  14488.000000   
3       20826.320000           44374.000000  38491.000000   
4         627.463333           57281.666667   2688.333333   
5         235.235000           49568.333333   3248.666667   
6       46961.000000           64971.000000  49858.000000   
7         367.617500           73419.750000   2872.250000   

        Existing Sushi Restaurant  Restaurant exclusive sushi  \
Labels                                                          
0                        0.025641                    0.871795   
1                        1.750000                   22.250000   
2                        3.500000                   12.500000   
3                        0.666667                   30.000000   
4                        1.000000                   12.666667   
5                        0.500000                   12.833333   
6                        1.000000                   12.000000   
7                        0.000000                    3.750000   

        Trasportation Facilities  Entertainment  
Labels                                           
0                            0.0       0.948718  
1                            0.0      13.250000  
2                            0.0      18.500000  
3                            0.0      15.000000  
4                            1.0       9.000000  
5                            0.0      14.666667  
6                            0.0      32.000000  
7                            0.0       3.750000

In [547]:
df_map = pd.concat([df_result, df_model], axis=1).reindex(df_result.index)
df_map.head()

County   Density  Medianhouseholdincome  Crime_sum  \
0       Albany County    570.74                56090.0       8025   
1     Allegany County     47.34                41305.0        456   
2        Bronx County  24118.20                34264.0      35255   
3       Broome County    280.56                44457.0       5169   
4  Cattaraugus County     61.31                42466.0        928   

   Existing Sushi Restaurant  Restaurant exclusive sushi  \
0                          4                          15   
1                          0                           1   
2                          1                          17   
3                          1                          18   
4                          0                           2   

   Trasportation Facilities  Entertainment   Density  Medianhouseholdincome  \
0                         0             21    570.74                56090.0   
1                         0              0     47.34                41305.0   
2                         0             13  24118.20                34264.0   
3                         0             28    280.56                44457.0   
4                         0              2     61.31                42466.0   

   Crime_sum  Existing Sushi Restaurant  Restaurant exclusive sushi  \
0       8025                          4                          15   
1        456                          0                           1   
2      35255                          1                          17   
3       5169                          1                          18   
4        928                          0                           2   

   Trasportation Facilities  Entertainment  Labels  
0                         0             21       2  
1                         0              0       0  
2                         0             13       3  
3                         0             28       5  
4                         0              2       0

# 5. Visualizing the result

In [548]:
df_map.head()

County   Density  Medianhouseholdincome  Crime_sum  \
0       Albany County    570.74                56090.0       8025   
1     Allegany County     47.34                41305.0        456   
2        Bronx County  24118.20                34264.0      35255   
3       Broome County    280.56                44457.0       5169   
4  Cattaraugus County     61.31                42466.0        928   

   Existing Sushi Restaurant  Restaurant exclusive sushi  \
0                          4                          15   
1                          0                           1   
2                          1                          17   
3                          1                          18   
4                          0                           2   

   Trasportation Facilities  Entertainment   Density  Medianhouseholdincome  \
0                         0             21    570.74                56090.0   
1                         0              0     47.34                41305.0   
2                         0             13  24118.20                34264.0   
3                         0             28    280.56                44457.0   
4                         0              2     61.31                42466.0   

   Crime_sum  Existing Sushi Restaurant  Restaurant exclusive sushi  \
0       8025                          4                          15   
1        456                          0                           1   
2      35255                          1                          17   
3       5169                          1                          18   
4        928                          0                           2   

   Trasportation Facilities  Entertainment  Labels  
0                         0             21       2  
1                         0              0       0  
2                         0             13       3  
3                         0             28       5  
4                         0              2       0

In [549]:
result_county= result[['County','County Latitude','County Lagitude']]
result_county.head()
#df_map = pd.concat([df_map, result_county], axis=1).reindex(df_result.index)

County  County Latitude  County Lagitude
0  Albany County        42.662094       -73.849075
1  Albany County        42.662094       -73.849075
2  Albany County        42.662094       -73.849075
3  Albany County        42.662094       -73.849075
4  Albany County        42.662094       -73.849075

In [559]:
df_map=pd.merge(result_county,df_map,on="County")
df_map

County  County Latitude_x  County Lagitude_x  \
0       Albany County          42.662094         -73.849075   
1       Albany County          42.662094         -73.849075   
2       Albany County          42.662094         -73.849075   
3       Albany County          42.662094         -73.849075   
4       Albany County          42.662094         -73.849075   
...               ...                ...                ...   
167287   Yates County          42.640000         -77.100000   
167288   Yates County          42.640000         -77.100000   
167289   Yates County          42.640000         -77.100000   
167290   Yates County          42.640000         -77.100000   
167291   Yates County          42.640000         -77.100000   

        County Latitude_y  County Lagitude_y  Density  Medianhouseholdincome  \
0               42.662094         -73.849075   570.74                56090.0   
1               42.662094         -73.849075   570.74                56090.0   
2               42.662094         -73.849075   570.74                56090.0   
3               42.662094         -73.849075   570.74                56090.0   
4               42.662094         -73.849075   570.74                56090.0   
...                   ...                ...      ...                    ...   
167287          42.640000         -77.100000    67.41                46822.0   
167288          42.640000         -77.100000    67.41                46822.0   
167289          42.640000         -77.100000    67.41                46822.0   
167290          42.640000         -77.100000    67.41                46822.0   
167291          42.640000         -77.100000    67.41                46822.0   

        Crime_sum  Existing Sushi Restaurant  Restaurant exclusive sushi  \
0            8025                          4                          15   
1            8025                          4                          15   
2            8025                          4                          15   
3            8025                          4                          15   
4            8025                          4                          15   
...           ...                        ...                         ...   
167287        187                          0                           5   
167288        187                          0                           5   
167289        187                          0                           5   
167290        187                          0                           5   
167291        187                          0                           5   

        Trasportation Facilities  Entertainment  Density  \
0                              0             21   570.74   
1                              0             21   570.74   
2                              0             21   570.74   
3                              0             21   570.74   
4                              0             21   570.74   
...                          ...            ...      ...   
167287                         0              8    67.41   
167288                         0              8    67.41   
167289                         0              8    67.41   
167290                         0              8    67.41   
167291                         0              8    67.41   

        Medianhouseholdincome  Crime_sum  Existing Sushi Restaurant  \
0                     56090.0       8025                          4   
1                     56090.0       8025                          4   
2                     56090.0       8025                          4   
3                     56090.0       8025                          4   
4                     56090.0       8025                          4   
...                       ...        ...                        ...   
167287                46822.0        187                          0   
167288                46822.0        187                          0   
167289                46

In [530]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(num_clusters)
ys = [i + x + (i*x)**2 for i in range(num_clusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(df_map['County Latitude'],df_map['County Lagitude'], df_map['County'], df_map['Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

## 6. Conclusion

In [554]:
conclusion # mean value in each cluster

Density  Medianhouseholdincome     Crime_sum  \
Labels                                                      
0         110.699744           47399.205128   1447.000000   
1        2514.385000           82205.500000  11487.500000   
2         659.880000           51731.000000  14488.000000   
3       20826.320000           44374.000000  38491.000000   
4         627.463333           57281.666667   2688.333333   
5         235.235000           49568.333333   3248.666667   
6       46961.000000           64971.000000  49858.000000   
7         367.617500           73419.750000   2872.250000   

        Existing Sushi Restaurant  Restaurant exclusive sushi  \
Labels                                                          
0                        0.025641                    0.871795   
1                        1.750000                   22.250000   
2                        3.500000                   12.500000   
3                        0.666667                   30.000000   
4                        1.000000                   12.666667   
5                        0.500000                   12.833333   
6                        1.000000                   12.000000   
7                        0.000000                    3.750000   

        Trasportation Facilities  Entertainment  
Labels                                           
0                            0.0       0.948718  
1                            0.0      13.250000  
2                            0.0      18.500000  
3                            0.0      15.000000  
4                            1.0       9.000000  
5                            0.0      14.666667  
6                            0.0      32.000000  
7                            0.0       3.750000

As shown in above table, the counties in New York are divided into 8 culsters:

Custer 0 has very little entertainment possibility, population density is only 110.70, excisting restaurant is also very low, that means it does not get good business clusters, so is not suitable

Cluster 3 and 6 have the highest crime rate, and the income level are also relvative low, so is not suitable

Culster 2 has the most sushi restaurant, and the cieme rate is the third highest, so is not suitable



Then there is only Cluster 1, 4, 5 and 7 left:

Cluster 1 has high population density, the Median household income is the highes, and there are high entertainment possibility before or after eating. The disadvantage of Cluster 1 is there are high crime rate and the competition with other sushi restaurant is relative high

Cluster 4 and cluster 5 are very similar. The values are in the middle. Cluster 4 has 1 transportation facilities (but since there are not so many transportation facilities found by foursquare, so the transportation facilities data is not so reliable to be compared). Cluster 5 has also lots of entertainment possiblity and the sushi restaurant is less than in cluster 4

Cluster 7 has low population density but high median householdincome, and there are no other sushi restaurant in this county. The disadvantage of Cluster 7 is there are also not so many entertainment possiblities.

Since the income of customers, entertainment possibilities, population density and the business clustering effect(more restaurant nearby, so the customer want to go to the area) are the key to my success, so in general, I would open the restaurant either in cluster 1 (Nassau, Richmond, Suffolk or Westchester County are suitable)

In [569]:
df_final=df_model
df_final = pd.concat([df_compare, df_final], axis=1).reindex(df_compare.index)
df_final.loc[(df_model['Labels'] == 1)]

County  Density  Medianhouseholdincome  Population  Crime_sum  \
29       Nassau County  2957.02                $93,613     1339532      13367   
42     Richmond County  4572.98                $71,084      468730       4789   
51      Suffolk County   629.31                $84,506     1493350      18157   
59  Westchester County  1898.23                $79,619      949113       9637   

    Accessories Store  Airport  American Restaurant  Animal Shelter  \
29                  0        0                    5               0   
42                  0        0                    0               0   
51                  1        0                    4               0   
59                  0        0                    6               0   

    Antique Shop  ...  Trasportation Facilities  Entertainment  Density  \
29             0  ...                         0             15  2957.02   
42             0  ...                         0              7  4572.98   
51             0  ...                         0             13   629.31   
59             0  ...                         0             18  1898.23   

    Medianhouseholdincome  Crime_sum  Existing Sushi Restaurant  \
29                93613.0      13367                          1   
42                71084.0       4789                          2   
51                84506.0      18157                          2   
59                79619.0       9637                          2   

    Restaurant exclusive sushi  Trasportation Facilities  Entertainment  \
29                          31                         0             15   
42                          20                         0              7   
51                          13                         0             13   
59                          25                         0             18   

    Labels  
29       1  
42       1  
51       1  
59       1  

[4 rows x 318 columns]